In [1]:
import micropip

%pip install lib3mf

micropip.add_mock_package("py-lib3mf", "2.4.1", modules={"py_lib3mf": '''from lib3mf import *'''})

%pip install build123d --force-reinstall
%pip install yacv-server

In [2]:
from build123d import *
from build123d import Shape
from OCP.TopLoc import TopLoc_Location
from OCP.TopoDS import TopoDS_Shape
from yacv_server import *
from IPython.display import HTML#, JSON, Latex, Markdown
import base64

In [3]:
def view(obj, c1 = (0.5,0.5,0.5,1), c2 = (0,0,0.5,1), c3 = (0.5,0,0.5,1)):

    obj = cad.get_shape(obj)

    if isinstance(obj, TopoDS_Shape):
        obj = Shape(obj).rotate(Axis.X, -90).wrapped
    elif isinstance(obj, TopLoc_Location):
        tmp_location = Location(obj)
        tmp_location.position = Vector(tmp_location.position.X, tmp_location.position.Z,
                                       -tmp_location.position.Y)
        tmp_location.orientation = Vector(tmp_location.orientation.X - 90, tmp_location.orientation.Y,
                                          tmp_location.orientation.Z)
        obj = tmp_location.wrapped
    
    temp = b''
    for i in tessellate.tessellate(obj, c1, c2, c3).save_to_bytes():
        temp += i
    display(HTML(f"""
        <html><body>
        </div>
        <script type="module" src="https://unpkg.com/@google/model-viewer/dist/model-viewer.min.js"></script>
        <model-viewer src="data:model/gltf-binary;base64,{base64.b64encode(temp).decode('utf-8')}" alt="A tea cup modelled in build123d" camera-controls style="width: 100%; height: 60vh;"></model-viewer>
        </body></html>"""))

In [4]:
phone_x, phone_y, phone_z = 73, 153, 9.3
corner_r, edge_r, cut_r = 11, 3, 1
thickness = 2
usb_x, usb_y = 14, 7
speaker_span, speaker_x, speaker_y = 37, 14, 4
camera_x, camera_y, camera_offset = phone_x-edge_r, 18.4, phone_y/2-22.4
buttons_offset, buttons_x, buttons_y = phone_y/2-60, 46, 3
mic_r, mic_offset = 2, 16.5-phone_x/2
notch_x, notch_y = 36, 4

with BuildPart() as phonecase:
    Box(phone_x, phone_y, phone_z)
    fillet(phonecase.edges().filter_by(Axis.Z), corner_r)
    # make phone body
    phonebody = fillet(phonecase.faces().filter_by(Axis.Z).edges(), edge_r)
    # extra extrude to make some thickness on top of shell
    extrude(phonecase.faces().filter_by(Axis.Z)[-1], thickness)
    # make case shell
    offset(phonecase.part, amount=thickness, openings=phonecase.faces().filter_by(Axis.Z)[0])
    # taper cut top opening of case
    extrude(phonebody.faces().filter_by(Axis.Z)[-1], thickness*2, taper=-60, mode=Mode.SUBTRACT)
    fillet(phonecase.edges().sort_by(Axis.Z)[-1], radius=2)
    with Locations((0,phone_y/2-edge_r,phone_z/2)) as speaker_notch:
        Box(notch_x, notch_y, thickness*2, mode=Mode.SUBTRACT)

    # cut bottom holes
    with BuildSketch(Plane(phonecase.faces().sort_by(Axis.Y)[0], x_dir=(1,0,0))) as bottom:
        RectangleRounded(usb_x, usb_y, cut_r)
        with GridLocations(speaker_span, 0, 2, 1) as speakers:
            RectangleRounded(speaker_x, speaker_y, cut_r)
    extrude(amount=-10, mode=Mode.SUBTRACT)
    temp_edges = phonecase.edges(Select.LAST).filter_by(Axis.X).group_by(Axis.Y)[1:3]
    fillet(temp_edges, radius=.8)

    # cut camera window
    with BuildSketch(Plane(phonecase.faces().sort_by(Axis.Z)[0], x_dir=(-1,0,0))) as back:
        with Locations((0,camera_offset)) as cameracut:
            Rectangle(camera_x, camera_y)
    extrude(amount=-thickness*2, mode=Mode.SUBTRACT)

    # cut buttons
    with BuildSketch(Plane(origin=(phone_x/2-1,buttons_offset,0), x_dir=(0,1,0),z_dir=(1,0,0))) as buttons:
        RectangleRounded(buttons_x, buttons_y, cut_r)
    extrude(amount=10, taper=-60, mode=Mode.SUBTRACT)
    button_round = phonecase.edges(Select.LAST).filter_by(Axis.Y).group_by(Axis.X)[-2]
    fillet(button_round, radius=1.2)

    # cut mic hole
    with BuildSketch(phonecase.faces().sort_by(Axis.Y)[-1]) as top:
        with Locations((1,mic_offset)) as mic_loc:
            Circle(mic_r)
    extrude(amount=-10, mode=Mode.SUBTRACT)

    # cut grips
    with BuildSketch(Plane(origin=(0,-phone_y/4,phone_z/2+thickness))) as grip_plane:
        with GridLocations(phone_x+2*thickness, 5, 2, 10) as grips:
            Rectangle(thickness/2, thickness/8)
    extrude(amount=-(phone_z+2*thickness), mode=Mode.SUBTRACT)
    fillet([phonecase.edges(Select.LAST).group_by(Axis.X)[i] for i in [0,-1]], thickness/4.01)

view(phonecase)